In [1]:
import nltk, csv, numpy
import re, sys
import os
import io
import codecs
from nltk.tokenize import word_tokenize
from nltk.probability import FreqDist
from collections import Counter
import numpy as np
import pandas as pd
import scipy
import matplotlib.pyplot as plt
import pyLDAvis
import pyLDAvis.gensim
import matplotlib.pyplot as plt
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.sentiment.vader import SentimentIntensityAnalyzer
from sklearn.metrics import accuracy_score
from nltk import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
import gensim
from gensim import corpora
import string
from textblob import Word
from nltk import sent_tokenize
from textblob import TextBlob
from nltk.corpus import stopwords
from nltk.corpus import stopwords
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
import re
import math
import warnings
from nltk.tag import pos_tag

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/urllib3/contrib/pyopenssl.py:46: DeprecationWarning: OpenSSL.rand is deprecated - you should use os.urandom instead
  import OpenSSL.SSL
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/scipy/sparse/sparsetools.py:21: DeprecationWarning: `scipy.sparse.sparsetools` is deprecated!
scipy.sparse.sparsetools is a private module for scipy.sparse, and should not be used.
  _deprecated()


In [2]:
survey = pd.read_csv('Project_Analytics.csv')

In [3]:
question_one = survey['What one thing can the organization do to make the business transformation successful?']
question_one.head()

0    Start to provide real opportunities for growth...
1    be better communicators we want to here from y...
2                 let me know what will change for me 
3       tell us what the new operation will look like 
4                         What’s really expected of me
Name: What one thing can the organization do to make the business transformation successful?, dtype: object

## Word Tokenization

#### What one thing can the organization do to make the business transformation successful?

In [4]:
survey['What one thing can the organization do to make the business transformation successful?'].dropna(inplace=True)
survey['tokenized_sent'] = survey['What one thing can the organization do to make the business transformation successful?'].apply(word_tokenize)
tokens_Q1 = survey['tokenized_sent']
tokens_Q1.head()

0    [Start, to, provide, real, opportunities, for,...
1    [be, better, communicators, we, want, to, here...
2         [let, me, know, what, will, change, for, me]
3    [tell, us, what, the, new, operation, will, lo...
4               [What, ’, s, really, expected, of, me]
Name: tokenized_sent, dtype: object

## Stop Words

In [5]:
stop_words = set(nltk.corpus.stopwords.words("english"))
print(stop_words)

{'needn', "you'd", "you'll", 'so', 'doesn', 'through', 'haven', 'below', "wouldn't", 'before', 'after', "hadn't", "she's", 'him', 'that', 'both', 'you', 'again', 'we', 'yours', 'but', 'how', 'own', 'doing', 'won', 'being', 'couldn', 'himself', 'had', 'it', 'wouldn', 'if', 'just', 'theirs', 'then', "you're", 'your', "you've", 'why', 'them', 'there', 'our', "didn't", 'did', 'during', 'with', 'each', "needn't", "mightn't", 'herself', 'o', 'which', 'do', 'between', 'not', 'can', 'more', "it's", 'weren', 'she', 'other', 'same', 't', 'ours', 'any', 'too', 'its', 'these', 'is', 'all', "weren't", 'in', 'some', 'hasn', 'further', 're', "doesn't", 'he', 'ourselves', 'shouldn', 'what', 'here', 'no', 'whom', 'at', 'than', 'they', 'only', 'the', 'few', 'has', 's', 'where', 'her', 'm', 'such', 'mustn', 'who', 'y', 'am', 'while', 'because', 'up', 'having', 'a', 'have', 'be', 'ain', 'itself', 'until', 'yourselves', 'over', 'about', 'nor', 'when', 'most', "haven't", 'shan', 'from', "wasn't", 'once', "m

### Word Removal

#### What one thing can the organization do to make the business transformation successful?

In [6]:
survey['What one thing can the organization do to make the business transformation successful?'] = survey['What one thing can the organization do to make the business transformation successful?'].fillna("")
survey['What one thing can the organization do to make the business transformation successful?'] = survey['What one thing can the organization do to make the business transformation successful?'].apply(lambda x: " ".join(x for x in x.split() if x not in stop_words))
stop_word_removal_one = survey['What one thing can the organization do to make the business transformation successful?']
stop_word_removal_one.head()

0    Start provide real opportunities growth lack j...
1                better communicators want consultants
2                                      let know change
3                      tell us new operation look like
4                               What’s really expected
Name: What one thing can the organization do to make the business transformation successful?, dtype: object

### Frequent Common Words

#### What one thing can the organization do to make the business transformation successful?

In [7]:
freq_question_one_words = pd.Series(' '.join(survey['What one thing can the organization do to make the business transformation successful?']).split()).value_counts()[:10]
freq_question_one_words

I          553
change     294
want       180
need       158
us         154
get        146
updates    132
team       129
share      116
people     113
dtype: int64

## Word Removal from Frequent Questions

#### What one thing can the organization do to make the business transformation successful?

In [8]:
survey['What one thing can the organization do to make the business transformation successful?'] = survey['What one thing can the organization do to make the business transformation successful?'].apply(lambda x: " ".join(x for x in x.split() if x not in freq_question_one_words))
survey['What one thing can the organization do to make the business transformation successful?'].head()

0    Start provide real opportunities growth lack j...
1                     better communicators consultants
2                                             let know
3                         tell new operation look like
4                               What’s really expected
Name: What one thing can the organization do to make the business transformation successful?, dtype: object

## Word Stemming

#### What one thing can the organization do to make the business transformation successful?

In [9]:
pst = PorterStemmer()
question_one_stemmed = pd.DataFrame(question_one)
question_one_stemmed['What one thing can the organization do to make the business transformation successful?'] = question_one_stemmed['What one thing can the organization do to make the business transformation successful?'].apply(lambda x: " ".join([pst.stem(word) for word in x.split()]))
stemmed_words_one = question_one_stemmed['What one thing can the organization do to make the business transformation successful?']
stemmed_words_one.head()

0    start to provid real opportun for growth lack ...
1    be better commun we want to here from you not ...
2                   let me know what will chang for me
3             tell us what the new oper will look like
4                            what’ realli expect of me
Name: What one thing can the organization do to make the business transformation successful?, dtype: object

## Word Lemmatization

#### What one thing can the organization do to make the business transformation successful?

In [10]:
survey['What one thing can the organization do to make the business transformation successful?'] = survey['What one thing can the organization do to make the business transformation successful?'].apply(lambda x: " ".join([Word(word).lemmatize() for word in x.split()]))
lemmatized_words_one = survey['What one thing can the organization do to make the business transformation successful?']
lemmatized_words_one.head()

0    Start provide real opportunity growth lack job...
1                       better communicator consultant
2                                             let know
3                         tell new operation look like
4                               What’s really expected
Name: What one thing can the organization do to make the business transformation successful?, dtype: object

## TF - IDF Weighting 

In [11]:
survey['What one thing can the organization do to make the business transformation successful?'] = survey['What one thing can the organization do to make the business transformation successful?'].str.replace('[^\w\s]','')
survey[survey['What one thing can the organization do to make the business transformation successful?'].notnull().dropna()]
survey['What one thing can the organization do to make the business transformation successful?'].head()

<input>:1: DeprecationWarning: invalid escape sequence \w
<input>:1: DeprecationWarning: invalid escape sequence \w
<input>:1: DeprecationWarning: invalid escape sequence \w
<input>:1: DeprecationWarning: invalid escape sequence \w
<input>:1: DeprecationWarning: invalid escape sequence \w
<input>:1: DeprecationWarning: invalid escape sequence \w
<input>:1: DeprecationWarning: invalid escape sequence \w
<input>:1: DeprecationWarning: invalid escape sequence \w
<input>:1: DeprecationWarning: invalid escape sequence \w
<ipython-input-11-84eb2362cfa2>:1: DeprecationWarning: invalid escape sequence \w
  survey['What one thing can the organization do to make the business transformation successful?'] = survey['What one thing can the organization do to make the business transformation successful?'].str.replace('[^\w\s]','')


0    Start provide real opportunity growth lack job...
1                       better communicator consultant
2                                             let know
3                         tell new operation look like
4                                Whats really expected
Name: What one thing can the organization do to make the business transformation successful?, dtype: object

#### What one thing can the organization do to make the business transformation successful?

In [12]:
TF_question_one = (survey['What one thing can the organization do to make the business transformation successful?']).apply(lambda x: pd.value_counts(x.split(" "))).sum(axis = 0).reset_index()

In [13]:
TF_question_one.columns = ['Words','TF']
TF_question_one.head()

Words    TF
0   provide  64.0
1  security   2.0
2      real  28.0
3     Start   6.0
4       job  56.0

In [14]:
for i,word in enumerate(TF_question_one['Words']):
  TF_question_one.loc[i, 'IDF'] = np.log(survey.shape[0]/(len(survey[survey['What one thing can the organization do to make the business transformation successful?'].str.contains(word)])))

In [15]:
TF_question_one.head()

Words    TF       IDF
0   provide  64.0  3.410748
1  security   2.0  6.907255
2      real  28.0  3.410748
3     Start   6.0  5.808643
4       job  56.0  3.457268

## Applying TF - IDF Weighting

#### What one thing can the organization do to make the business transformation successful?

In [16]:
TF_question_one['TFIDF'] = TF_question_one['TF'] * TF_question_one['IDF']
TF_question_one.head()

Words    TF       IDF       TFIDF
0   provide  64.0  3.410748  218.287846
1  security   2.0  6.907255   13.814510
2      real  28.0  3.410748   95.500933
3     Start   6.0  5.808643   34.851857
4       job  56.0  3.457268  193.606986

## Vectorizer Applied on Stemmed Words

#### What one thing can the organization do to make the business transformation successful?

In [17]:
vectorizer = TfidfVectorizer(stop_words ='english')
matrix = vectorizer.fit_transform(question_one_stemmed['What one thing can the organization do to make the business transformation successful?']).todense()

In [18]:
matrix = pd.DataFrame(matrix, columns=vectorizer.get_feature_names())

In [19]:
top_words_question_one = matrix.sum(axis=0).sort_values(ascending=False)
top_words_question_one.head()

thi       87.796037
chang     86.158895
share     62.806563
commun    53.084032
team      50.180266
dtype: float64

## Vectorizer on Lemmatized Words

#### What one thing can the organization do to make the business transformation successful?

In [20]:
vectorizer = TfidfVectorizer(stop_words ='english')
matrix_lemmatize = vectorizer.fit_transform(survey['What one thing can the organization do to make the business transformation successful?']).todense()

In [21]:
matrix_lemmatize = pd.DataFrame(matrix_lemmatize, columns=vectorizer.get_feature_names())

In [22]:
top_words_question_one = matrix_lemmatize.sum(axis=0).sort_values(ascending=False)
top_words_question_one.head()

training         40.936630
communication    36.733231
plan             36.680724
provide          36.089533
project          36.035512
dtype: float64

## Sentiment Analysis

#### What one thing can the organization do to make the business transformation successful?

In [24]:
with open('Project_Analytics.csv') as f:
     survey = csv.reader(f, delimiter=',')
     next(survey)
     for row in survey:
        sentences = sent_tokenize(row[35])
        sid = SentimentIntensityAnalyzer()
        for sentence in sentences:
            print('\n' + sentence)
        ss = sid.polarity_scores(sentence)
        for k in sorted(ss):
            print('{0}: {1}, '.format(k, ss[k]))


Start to provide real opportunities for growth lack of job security
compound: 0.6486, 
neg: 0.136, 
neu: 0.414, 
pos: 0.45, 

be better communicators we want to here from you not consultants
compound: 0.4939, 
neg: 0.0, 
neu: 0.682, 
pos: 0.318, 

let me know what will change for me
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

tell us what the new operation will look like
compound: 0.3612, 
neg: 0.0, 
neu: 0.762, 
pos: 0.238, 

What’s really expected of me
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

don’t just speak to my manager speak to me and when is training
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

start to reinvest in us - we are supposed to be your most important asset - prove it
compound: 0.5956, 
neg: 0.0, 
neu: 0.742, 
pos: 0.258, 

Why are we doing this and when is going to affect me
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

will this address problems with you paying unfair wages  and paying men more than women doing the same job and will benefits


I would not go out of my way to learn more I want to hear about what this means to me and my team - what will happen to our jobs
compound: 0.1513, 
neg: 0.0, 
neu: 0.944, 
pos: 0.056, 

I listened and felt like no one wanted to hear from me a I wasted my time
compound: -0.4404, 
neg: 0.286, 
neu: 0.582, 
pos: 0.132, 

 what will happen with my role I've been hear for 20 years
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

my VP lies to us so nothing I don’t trust anymore
compound: -0.6971, 
neg: 0.419, 
neu: 0.581, 
pos: 0.0, 

bring back benefits we used to have
compound: 0.3818, 
neg: 0.0, 
neu: 0.698, 
pos: 0.302, 

nothing
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

make us part of the change
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

provide time for us to read the updates and create videos
compound: 0.2732, 
neg: 0.0, 
neu: 0.826, 
pos: 0.174, 

WIIFM
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

How will my performance be measured and what will I do in the f

pos: 0.512, 

I bought this communication you providing in our team meeting to give people something to think on.

I liked it because it's bite size it's easier for people to understand when its just a couple pieces of information rather than an entire licorice stick.

My only complaint is that no one knows what will happen to our seniority and current ways of operation
compound: -0.5267, 
neg: 0.206, 
neu: 0.794, 
pos: 0.0, 

I have no idea what transformation you're talking about
compound: -0.296, 
neg: 0.239, 
neu: 0.761, 
pos: 0.0, 

I love these updates keep them coming , I think I am addicted to them and want more.

I want to subscribe to get more updates and we want to see the new hierarchies and new production schedules.
compound: 0.1531, 
neg: 0.0, 
neu: 0.867, 
pos: 0.133, 

If you are looking for a less messy transformation, get leaders to tell us what to expect,  I highly recommend!
compound: 0.2211, 
neg: 0.104, 
neu: 0.751, 
pos: 0.145, 

I might be mistaken, but it appea


What change management being planned and executed - let's not make the newspapers like last time
compound: 0.3612, 
neg: 0.0, 
neu: 0.848, 
pos: 0.152, 

really, you never asked me before.

If you really want to know then tell us when we will find out about keeping our jobs
compound: 0.1513, 
neg: 0.0, 
neu: 0.914, 
pos: 0.086, 

Enjoying things so far, but I want more clarity on why were doing this.

What are the benefits?
compound: 0.3818, 
neg: 0.0, 
neu: 0.536, 
pos: 0.464, 

What will training look like for us?
compound: 0.3612, 
neg: 0.0, 
neu: 0.706, 
pos: 0.294, 

Took me one or two updates to get used what this is.

But now aim hooked and want to get training
compound: 0.0772, 
neg: 0.0, 
neu: 0.86, 
pos: 0.14, 

This transformation  is not as described.

Paid a good chunk of cash for nothing from the consultants yet.

I want to hear from our leaders
compound: 0.0772, 
neg: 0.0, 
neu: 0.794, 
pos: 0.206, 

keep updates coming and stay the course, no matter how long.
compound:


How can you make sure that my team members get recognized for success, and that my team participates on this for their career growth.

How are the change agents on this?
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

 When we launch this major initiative what are the benefits ?
compound: 0.3818, 
neg: 0.0, 
neu: 0.776, 
pos: 0.224, 

Share what is  key to its success?
compound: 0.7096, 
neg: 0.0, 
neu: 0.459, 
pos: 0.541, 

This is the first time I've really been misled by leaders about a program.

Please talk to us honestly
compound: 0.6486, 
neg: 0.0, 
neu: 0.361, 
pos: 0.639, 

I want to hear how you will craft a win-win for each group involved and impacted.
compound: 0.0772, 
neg: 0.0, 
neu: 0.909, 
pos: 0.091, 

You HAVE to communicate more.

And make training of this change  the BEST EVER!

!
compound: 0.0, 
neg: 0.0, 
neu: 0.0, 
pos: 0.0, 

think about  how this affects groups both within and outside the company
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

Highly recomm

...

compound: 0.4019, 
neg: 0.0, 
neu: 0.597, 
pos: 0.403, 

start change management activities right now on this implementation
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

plan on the capability of the organization to change
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

help us understand the vision
compound: 0.5719, 
neg: 0.0, 
neu: 0.39, 
pos: 0.61, 

Confirm "What's the business case is"
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

share how we get trained
compound: 0.296, 
neg: 0.0, 
neu: 0.645, 
pos: 0.355, 

CREATE a clear vision of this change
compound: 0.7531, 
neg: 0.0, 
neu: 0.288, 
pos: 0.712, 

create a sense of urgency
compound: 0.2732, 
neg: 0.0, 
neu: 0.588, 
pos: 0.412, 

share how values and behaviours will change
compound: 0.5994, 
neg: 0.0, 
neu: 0.505, 
pos: 0.495, 

tell me the advantages of this change
compound: 0.3612, 
neg: 0.0, 
neu: 0.706, 
pos: 0.294, 

make sure leaders focused on real change
compound: 0.5994, 
neg: 0.0, 
neu: 0.505, 
pos: 0.495,

compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

get leaders and employees onboard early for a successful implementation
compound: 0.5859, 
neg: 0.0, 
neu: 0.678, 
pos: 0.322, 

honest talk communications and let us provide feedback.
compound: 0.5106, 
neg: 0.0, 
neu: 0.68, 
pos: 0.32, 

Executive Leaders  must be committed to support
compound: 0.5859, 
neg: 0.0, 
neu: 0.51, 
pos: 0.49, 

Provide better planned our and varied communications
compound: 0.4404, 
neg: 0.0, 
neu: 0.674, 
pos: 0.326, 

confirm when the re-organization will happen
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

successfully work as a team and stay the course
compound: 0.4939, 
neg: 0.0, 
neu: 0.686, 
pos: 0.314, 

.

Listen to people doing the work to confirm readiness
compound: 0.25, 
neg: 0.0, 
neu: 0.8, 
pos: 0.2, 

Involve the business get them to sign off on transition plans development
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

Involve employees and cocreate for successful change
compound: 0.5

compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

Training lectures don’t cut it for me.

I need more hands on approach.
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

Testing scenarios are not relevant to our real life situations.
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

My team is more than willing to engage with the project team.

Please involve them in the process.
compound: 0.3182, 
neg: 0.0, 
neu: 0.685, 
pos: 0.315, 

Communication, communication, and communication!
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

The project team need to ask for and receive more feedback from people impacted by the change.
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

Do we need to go this fast?!

Slow than and make sure we are going the right way.
compound: 0.3182, 
neg: 0.0, 
neu: 0.813, 
pos: 0.187, 

Change is a must for us.

The HR team needs to be engaged early on
compound: 0.4019, 
neg: 0.0, 
neu: 0.748, 
pos: 0.252, 

Customized emails so I would know what is changing f


Thanks for the email updates.
compound: 0.4404, 
neg: 0.0, 
neu: 0.58, 
pos: 0.42, 

You have created lots of headaches for my team.

They have jobs to do!
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

Do this right the first time.

Plan accordingly.
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

Our leaders only think about the financial gains.

Why do we need this change now?
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

We have been always reactive and waited for problems.

Let's be proactive for a change.
compound: 0.4215, 
neg: 0.0, 
neu: 0.588, 
pos: 0.412, 

Just keep us informed.
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

This is the first time we are experiencing a project with this magnitude.

You need to engage many people.
compound: 0.34, 
neg: 0.0, 
neu: 0.676, 
pos: 0.324, 

Count me in if you need support.

How do I get involved?
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

It doesn't work if you just install a new technology.

Many organizational

More honesty with your communications.
compound: 0.5413, 
neg: 0.0, 
neu: 0.534, 
pos: 0.466, 

HR team needs to be engaged early on.

They need to be consulted if roles are changing.
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

Generic communications, technical jargon.
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

Train people on the job.

Lecture does not work here.
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

I am not sure if we need this project and I really don't need all these emails in my inbox.
compound: -0.2411, 
neg: 0.103, 
neu: 0.897, 
pos: 0.0, 

I don't see consistency in the messages that we receive from different managers.
compound: 0.0, 
neg: 0.0, 
neu: 1.0, 
pos: 0.0, 

We are too eager to grab the new shiny things, without stopping and considering how we are doing with what we already have.
compound: 0.4486, 
neg: 0.0, 
neu: 0.842, 
pos: 0.158, 

The more we have implemented new technologies, the more siloed we get.

We need more teamwork.
compound: 0.0

# Topic Modeling 

#### What one thing can the organization do to make the business transformation successful?

In [25]:
import bigfloat
bigfloat.exp(5000,bigfloat.precision(100))

BigFloat.exact('2.9676283840236670689662968052896e+2171', precision=100)

In [27]:
survey = pd.read_csv('Project_Analytics.csv')
question_one = survey['What one thing can the organization do to make the business transformation successful?'].str.replace('[^\w\s]','')
question_one = survey[survey['What one thing can the organization do to make the business transformation successful?'].notnull().dropna()]
question_one = survey['What one thing can the organization do to make the business transformation successful?'].fillna("")

<input>:2: DeprecationWarning: invalid escape sequence \w
<input>:2: DeprecationWarning: invalid escape sequence \w
<input>:2: DeprecationWarning: invalid escape sequence \w
<input>:2: DeprecationWarning: invalid escape sequence \w
<input>:2: DeprecationWarning: invalid escape sequence \w
<input>:2: DeprecationWarning: invalid escape sequence \w
<input>:2: DeprecationWarning: invalid escape sequence \w
<input>:2: DeprecationWarning: invalid escape sequence \w
<input>:2: DeprecationWarning: invalid escape sequence \w
<ipython-input-27-422f7387017e>:2: DeprecationWarning: invalid escape sequence \w
  question_one = survey['What one thing can the organization do to make the business transformation successful?'].str.replace('[^\w\s]','')


In [28]:
stop = set(stopwords.words('english'))
exclude = set(string.punctuation) 
lemma = WordNetLemmatizer()

In [29]:
def clean(survey):
    stop_free = " ".join([i for i in survey.lower().split() if i not in stop])
    punc_free = ''.join(ch for ch in stop_free if ch not in exclude)
    normalized = " ".join(lemma.lemmatize(word) for word in punc_free.split())
    return(normalized)        

In [30]:
survey_prepared = [clean(survey).split() for survey in question_one]
survey_cleaned = []
for survey in survey_prepared:   
    clean_survey = []  
    for survey_word in survey:        
        if(len(survey_word)>2):
            clean_survey.append(survey_word)
            if(len(clean_survey) >0):
                survey_cleaned.append(clean_survey)

survey_cleaned

[['start',
  'provide',
  'real',
  'opportunity',
  'growth',
  'lack',
  'job',
  'security'],
 ['start',
  'provide',
  'real',
  'opportunity',
  'growth',
  'lack',
  'job',
  'security'],
 ['start',
  'provide',
  'real',
  'opportunity',
  'growth',
  'lack',
  'job',
  'security'],
 ['start',
  'provide',
  'real',
  'opportunity',
  'growth',
  'lack',
  'job',
  'security'],
 ['start',
  'provide',
  'real',
  'opportunity',
  'growth',
  'lack',
  'job',
  'security'],
 ['start',
  'provide',
  'real',
  'opportunity',
  'growth',
  'lack',
  'job',
  'security'],
 ['start',
  'provide',
  'real',
  'opportunity',
  'growth',
  'lack',
  'job',
  'security'],
 ['start',
  'provide',
  'real',
  'opportunity',
  'growth',
  'lack',
  'job',
  'security'],
 ['better', 'communicator', 'want', 'consultant'],
 ['better', 'communicator', 'want', 'consultant'],
 ['better', 'communicator', 'want', 'consultant'],
 ['better', 'communicator', 'want', 'consultant'],
 ['let', 'know', 'ch

In [31]:
from gensim import corpora
dictionary = corpora.Dictionary(survey_cleaned)
corpus = [dictionary.doc2bow(survey) for survey in survey_cleaned]
import pickle
pickle.dump(corpus, open('corpus.pkl', 'wb'))
dictionary.save('dictionary.gensim')

In [32]:
import pickle
from scipy.special import expit
import decimal
pickle.dump(corpus, open('corpus.pkl', 'wb'))
dictionary.save('dictionary.gensim')

In [36]:
ldamodel = gensim.models.ldamulticore.LdaMulticore(corpus, 
    id2word=dictionary, num_topics=3, chunksize=1800, passes=20, 
    workers=1, eval_every=1, iterations=1000)

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

...

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

In [37]:
print(ldamodel.print_topics(num_topics=3, num_words=3))

[(0, '0.029*"update" + 0.023*"know" + 0.020*"team"'), (1, '0.042*"change" + 0.024*"process" + 0.022*"plan"'), (2, '0.037*"change" + 0.025*"need" + 0.022*"business"')]


In [38]:
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(ldamodel, corpus, dictionary)
vis

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2     -0.045138 -0.215100       1        1  35.609875
1     -0.193809  0.141203       2        1  35.289158
0      0.238947  0.073897       3        1  29.100973, topic_info=     Category         Freq           Term        Total  loglift  logprob
term                                                                    
137   Default  1010.000000        process  1010.000000  30.0000  30.0000
577   Default   907.000000           plan   907.000000  29.0000  29.0000
166   Default  1428.000000         update  1428.000000  28.0000  28.0000
13    Default   952.000000           know   952.000000  27.0000  27.0000
683   Default   724.000000     management   724.000000  26.0000  26.0000
140   Default   690.000000           good   690.000000  25.0000  25.0000
375   Default  1123.000000       business  1123.000000  24.0000  24.0000
472   Default   605.000000        support   605.000000  23.0000  23.0000
105   Default   483.000000            one   483.000000  22.0000  22.0000
67    Default  1525.000000         people  1525.000000  21.0000  21.0000
107   Default   803.000000          thing   803.000000  20.0000  20.0000
11    Default  1185.000000           want  1185.000000  19.0000  19.0000
978   Default   402.000000     technology   402.000000  18.0000  18.0000
331   Default   472.000000          focus   472.000000  17.0000  17.0000
86    Default   874.000000         leader   874.000000  16.0000  16.0000
383   Default   361.000000           many   361.000000  15.0000  15.0000
240   Default   351.000000         always   351.000000  14.0000  14.0000
268   Default   429.000000          think   429.000000  13.0000  13.0000
93    Default   339.000000           find   339.000000  12.0000  12.0000
1     Default   640.000000            job   640.000000  11.0000  11.0000
702   Default   391.000000         system   391.000000  10.0000  10.0000
237   Default   321.000000    communicate   321.000000   9.0000   9.0000
110   Default   992.000000           make   992.000000   8.0000   8.0000
317   Default   421.000000      different   421.000000   7.0000   7.0000
5     Default   326.000000           real   326.000000   6.0000   6.0000
403   Default   268.000000           best   268.000000   5.0000   5.0000
216   Default   268.000000       question   268.000000   4.0000   4.0000
799   Default   316.000000         senior   316.000000   3.0000   3.0000
70    Default   311.000000       changing   311.000000   2.0000   2.0000
94    Default   310.000000       everyone   310.000000   1.0000   1.0000
...       ...          ...            ...          ...      ...      ...
1989   Topic3    94.994102          eager    95.754265   1.2264  -5.8886
1284   Topic3   107.282471       director   108.361061   1.2244  -5.7670
379    Topic3    99.122581           seem   100.021004   1.2254  -5.8461
268    Topic3   394.641815          think   429.499207   1.1498  -4.4645
13     Topic3   797.050720           know   952.486267   1.0562  -3.7615
317    Topic3   372.084351      different   421.275146   1.1102  -4.5233
124    Topic3   181.272888        message   195.581741   1.1584  -5.2425
166    Topic3  1009.843750         update  1428.111450   0.8878  -3.5249
107    Topic3   606.151550          thing   803.645386   0.9524  -4.0353
1      Topic3   465.806274            job   640.864258   0.9154  -4.2987
134    Topic3   190.913773         impact   221.169891   1.0873  -5.1906
297    Topic3   250.008438           love   320.593750   0.9857  -4.9210
650    Topic3   182.911362         around   223.739441   1.0329  -5.2335
215    Topic3   237.109787       feedback   331.025909   0.9007  -4.9739
4      Topic3   352.429047        provide   593.902466   0.7125  -4.5776
135    Topic3   701.296997           team  1643.763550   0.3826  -3.8895
80     Topic3   234.878342           this   338.469543   0.8690  -4.9834
143    Topic3   554.960876           

#### Topic Analysis on TF - IDF: What one thing can the organization do to make the business transformation successful?

In [39]:
from gensim import corpora, models

In [40]:
corpus = [dictionary.doc2bow(survey) for survey in survey_cleaned]
corpus[4310]

[(78, 1), (110, 1), (140, 1), (160, 1), (305, 1), (486, 1), (1196, 1)]

In [41]:
tfidf = models.TfidfModel(corpus)
corpus_tfidf = tfidf[corpus]

In [42]:
from pprint import pprint

In [43]:
for doc in corpus_tfidf:
    pprint(doc)
    break

[(0, 0.42182466379276856),
 (1, 0.26715768049667027),
 (2, 0.37672703304733746),
 (3, 0.28954273768175676),
 (4, 0.23958376269952056),
 (5, 0.3085440192415464),
 (6, 0.5343671119247275),
 (7, 0.2945920415236949)]


#### LDA with Bag of Words: What one thing can the organization do to make the business transformation successful?

In [44]:
lda_model = gensim.models.LdaMulticore(corpus, num_topics=3, id2word=dictionary, passes=2, workers=2)

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

...

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

In [45]:
for idx, topic in lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.036*"need" + 0.032*"change" + 0.017*"people" + 0.017*"know" + 0.014*"team" + 0.014*"communication" + 0.011*"project" + 0.011*"leader" + 0.010*"training" + 0.010*"program"
Topic: 1 
Words: 0.042*"change" + 0.025*"time" + 0.024*"new" + 0.021*"people" + 0.019*"process" + 0.013*"business" + 0.013*"way" + 0.012*"thing" + 0.012*"plan" + 0.011*"system"
Topic: 2 
Words: 0.024*"update" + 0.024*"project" + 0.022*"need" + 0.019*"change" + 0.018*"team" + 0.017*"make" + 0.015*"share" + 0.015*"sure" + 0.014*"want" + 0.014*"get"


In [46]:
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, dictionary)
vis

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2      0.099224  0.099127       1        1  34.275688
1     -0.145545  0.027332       2        1  33.496399
0      0.046321 -0.126459       3        1  32.227905, topic_info=     Category         Freq           Term        Total  loglift  logprob
term                                                                    
17    Default  1193.000000            new  1193.000000  30.0000  30.0000
143   Default  1313.000000           time  1313.000000  29.0000  29.0000
137   Default  1016.000000        process  1016.000000  28.0000  28.0000
186   Default   535.000000            way   535.000000  27.0000  27.0000
702   Default   458.000000         system   458.000000  26.0000  26.0000
13    Default   878.000000           know   878.000000  25.0000  25.0000
146   Default  2679.000000           need  2679.000000  24.0000  24.0000
133   Default   780.000000           sure   780.000000  23.0000  23.0000
86    Default   707.000000         leader   707.000000  22.0000  22.0000
76    Default  1561.000000        project  1561.000000  21.0000  21.0000
517   Default   413.000000           tool   413.000000  20.0000  20.0000
67    Default  1636.000000         people  1636.000000  19.0000  19.0000
190   Default   290.000000          level   290.000000  18.0000  18.0000
110   Default  1008.000000           make  1008.000000  17.0000  17.0000
107   Default   645.000000          thing   645.000000  16.0000  16.0000
166   Default  1544.000000         update  1544.000000  15.0000  15.0000
978   Default   412.000000     technology   412.000000  14.0000  14.0000
123   Default   495.000000       involved   495.000000  13.0000  13.0000
502   Default   205.000000         expect   205.000000  12.0000  12.0000
130   Default   977.000000          share   977.000000  11.0000  11.0000
12    Default  3601.000000         change  3601.000000  10.0000  10.0000
689   Default   208.000000        testing   208.000000   9.0000   9.0000
99    Default   166.000000        visible   166.000000   8.0000   8.0000
292   Default   234.000000         create   234.000000   7.0000   7.0000
24    Default   371.000000        manager   371.000000   6.0000   6.0000
1043  Default   170.000000         engage   170.000000   5.0000   5.0000
191   Default   465.000000            see   465.000000   4.0000   4.0000
799   Default   394.000000         senior   394.000000   3.0000   3.0000
98    Default   153.000000            top   153.000000   2.0000   2.0000
237   Default   310.000000    communicate   310.000000   1.0000   1.0000
...       ...          ...            ...          ...      ...      ...
146    Topic3  1382.278198           need  2679.077637   0.4706  -3.3130
191    Topic3   316.381744            see   465.599304   0.7460  -4.7876
86     Topic3   424.396759         leader   707.477173   0.6213  -4.4939
799    Topic3   260.992584         senior   394.621552   0.7189  -4.9800
204    Topic3   118.919746          first   152.510681   0.8836  -5.7661
55     Topic3    93.423691         shared   111.939163   0.9515  -6.0074
208    Topic3   337.327637       employee   598.128418   0.5596  -4.7235
878    Topic3    83.629143       impacted    98.020386   0.9736  -6.1181
233    Topic3   242.033356           role   410.843414   0.6032  -5.0554
12     Topic3  1198.866699         change  3601.873047   0.0323  -3.4554
67     Topic3   646.505798         people  1636.940674   0.2033  -4.0729
152    Topic3   134.164917       customer   186.947144   0.8006  -5.6455
321    Topic3   389.877502        program   829.761902   0.3770  -4.5787
78     Topic3   525.250122  communication  1297.715210   0.2279  -4.2807
472    Topic3   314.959930        support   625.258423   0.4466  -4.7921
26     Topic3   390.872742       training   859.059204   0.3449  -4.5761
135    Topic3   534.133606           team  1595.971191   0.0377  -4.2639
683    Topic3   360.730743     manage

#### LDA with TF - IDF: What one thing can the organization do to make the business transformation successful?

In [47]:
lda_model_tfidf = gensim.models.LdaMulticore(corpus_tfidf, num_topics=3, id2word=dictionary, passes=2, workers=4)

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

...

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin 

In [48]:
for idx, topic in lda_model_tfidf.print_topics(-1):
    print('Topic: {} Word: {}'.format(idx, topic))

Topic: 0 Word: 0.013*"share" + 0.011*"business" + 0.011*"team" + 0.009*"change" + 0.008*"focus" + 0.008*"get" + 0.008*"want" + 0.008*"project" + 0.007*"training" + 0.007*"make"
Topic: 1 Word: 0.011*"update" + 0.011*"change" + 0.008*"communication" + 0.008*"people" + 0.008*"leader" + 0.008*"provide" + 0.007*"need" + 0.007*"keep" + 0.007*"share" + 0.007*"make"
Topic: 2 Word: 0.017*"change" + 0.015*"plan" + 0.012*"need" + 0.010*"management" + 0.008*"team" + 0.008*"get" + 0.007*"share" + 0.006*"new" + 0.006*"communication" + 0.006*"create"


In [49]:
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model_tfidf, corpus, dictionary)
vis

/Users/josenoriegaportilla/anaconda3/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1     -0.030625 -0.088145       1        1  37.751759
0     -0.069439  0.067961       2        1  33.291641
2      0.100064  0.020184       3        1  28.956604, topic_info=     Category         Freq            Term        Total  loglift  logprob
term                                                                     
577   Default   764.000000            plan   764.000000  30.0000  30.0000
292   Default   257.000000          create   257.000000  29.0000  29.0000
331   Default   407.000000           focus   407.000000  28.0000  28.0000
683   Default   535.000000      management   535.000000  27.0000  27.0000
75    Default   272.000000         nothing   272.000000  26.0000  26.0000
375   Default   724.000000        business   724.000000  25.0000  25.0000
1322  Default   159.000000           ready   159.000000  24.0000  24.0000
496   Default   255.000000          coming   255.000000  23.0000  23.0000
768   Default   275.000000         success   275.000000  22.0000  22.0000
818   Default   203.000000         explain   203.000000  21.0000  21.0000
150   Default   182.000000         prepare   182.000000  20.0000  20.0000
242   Default   191.000000         engaged   191.000000  19.0000  19.0000
84    Default   199.000000           still   199.000000  18.0000  18.0000
127   Default   150.000000           heard   150.000000  17.0000  17.0000
383   Default   256.000000            many   256.000000  16.0000  16.0000
12    Default  1382.000000          change  1382.000000  15.0000  15.0000
108   Default   395.000000           whats   395.000000  14.0000  14.0000
146   Default   966.000000            need   966.000000  13.0000  13.0000
215   Default   400.000000        feedback   400.000000  12.0000  12.0000
305   Default   309.000000      understand   309.000000  11.0000  11.0000
86    Default   584.000000          leader   584.000000  10.0000  10.0000
73    Default   462.000000            keep   462.000000   9.0000   9.0000
143   Default   581.000000            time   581.000000   8.0000   8.0000
429   Default   117.000000             bad   117.000000   7.0000   7.0000
138   Default   163.000000        decision   163.000000   6.0000   6.0000
1002  Default    99.000000       implement    99.000000   5.0000   5.0000
92    Default   294.000000         working   294.000000   4.0000   4.0000
442   Default    94.000000           might    94.000000   3.0000   3.0000
1025  Default   117.000000           state   117.000000   2.0000   2.0000
54    Default   285.000000             far   285.000000   1.0000   1.0000
...       ...          ...             ...          ...      ...      ...
146    Topic3   413.623016            need   966.411133   0.3907  -4.4125
55     Topic3    72.946808          shared    97.401550   0.9503  -6.1478
92     Topic3   163.906815         working   294.736420   0.6526  -5.3382
263    Topic3    82.855858       happening   117.542679   0.8897  -6.0204
186    Topic3   195.972000             way   420.603333   0.4757  -5.1595
87     Topic3   138.528549          listen   258.210266   0.6167  -5.5064
15     Topic3   197.013245            like   438.125488   0.4401  -5.1542
89     Topic3   274.588593             get   798.930908   0.1714  -4.8222
565    Topic3    63.748520           sense    82.246109   0.9846  -6.2825
143    Topic3   214.774582            time   581.260681   0.2438  -5.0679
135    Topic3   286.651123            team   969.644409   0.0207  -4.7792
933    Topic3    78.797821     development   116.908279   0.8449  -6.0706
408    Topic3   191.454575  transformation   517.405823   0.2452  -5.1828
17     Topic3   221.514175             new   678.299377   0.1203  -5.0370
78     Topic3   219.965500   communication   772.606750  -0.0169  -5.0440
130    Topic3   247.757828           share  1063.710815  -0.2177  -4.9250
114    Topic3   139.466202         company   346.686279   0.3

#### Performance based on LDA Bag of Words: What one thing can the organization do to make the business transformation successful?

In [50]:
for index, score in sorted(lda_model[corpus[4310]], key=lambda tup: -1*tup[1]):
    print("\nScore: {}\t \nTopic: {}".format(score, lda_model.print_topic(index, 10)))


Score: 0.7161075472831726	 
Topic: 0.036*"need" + 0.032*"change" + 0.017*"people" + 0.017*"know" + 0.014*"team" + 0.014*"communication" + 0.011*"project" + 0.011*"leader" + 0.010*"training" + 0.010*"program"

Score: 0.23253758251667023	 
Topic: 0.024*"update" + 0.024*"project" + 0.022*"need" + 0.019*"change" + 0.018*"team" + 0.017*"make" + 0.015*"share" + 0.015*"sure" + 0.014*"want" + 0.014*"get"

Score: 0.05135488882660866	 
Topic: 0.042*"change" + 0.025*"time" + 0.024*"new" + 0.021*"people" + 0.019*"process" + 0.013*"business" + 0.013*"way" + 0.012*"thing" + 0.012*"plan" + 0.011*"system"


#### Performance Based on LDA TF - IDF: What one thing can the organization do to make the business transformation successful?

In [51]:
for index, score in sorted(lda_model_tfidf[corpus[4310]], key=lambda tup: -1*tup[1]):
    print("\nScore: {}\t \nTopic: {}".format(score, lda_model_tfidf.print_topic(index, 10)))


Score: 0.9047790765762329	 
Topic: 0.011*"update" + 0.011*"change" + 0.008*"communication" + 0.008*"people" + 0.008*"leader" + 0.008*"provide" + 0.007*"need" + 0.007*"keep" + 0.007*"share" + 0.007*"make"

Score: 0.04997555911540985	 
Topic: 0.013*"share" + 0.011*"business" + 0.011*"team" + 0.009*"change" + 0.008*"focus" + 0.008*"get" + 0.008*"want" + 0.008*"project" + 0.007*"training" + 0.007*"make"

Score: 0.045245397835969925	 
Topic: 0.017*"change" + 0.015*"plan" + 0.012*"need" + 0.010*"management" + 0.008*"team" + 0.008*"get" + 0.007*"share" + 0.006*"new" + 0.006*"communication" + 0.006*"create"
